<a href="https://colab.research.google.com/github/inzamamulDU/chicago-taxi-trip/blob/main/Chicago_Taxi_Trips.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Before you begin


1.   Use the [Cloud Resource Manager](https://console.cloud.google.com/cloud-resource-manager) to Create a Cloud Platform project if you do not already have one.
2.   [Enable billing](https://support.google.com/cloud/answer/6293499#enable-billing) for the project.
3.   [Enable BigQuery](https://console.cloud.google.com/flows/enableapi?apiid=bigquery) APIs for the project.

# Provide credentials to the runtime

In [1]:
from google.colab import auth
auth.authenticate_user()
print('Authenticated')

Authenticated


In [2]:
import pandas as pd
from google.colab import files

## Optional: Enable data table display

Colab includes the ``google.colab.data_table`` package that can be used to display large pandas dataframes as an interactive data table.
It can be enabled with:

In [3]:
%reload_ext google.colab.data_table

# Use BigQuery via magics

The `google.cloud.bigquery` library also includes a magic command which runs a query and either displays the result or saves it to a variable as a `DataFrame`.

In [4]:
%reload_ext google.cloud.bigquery

# Understand the data

**Note that each time you run a query, you have to replace your-project-id placeholder with your own Cloud Platform project ID.**

We run our first query to check the total number of rows in the dataset.

In [10]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*) as total_rows
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`

total_rows
0   197421650

We also want to find out the total number of non-blank rows for the `pickup_location` and `dropoff_location` columns, and total number of non-zero rows for the `trip_seconds` and `trip_miles` columns. For each of these cases, we modify the above query with appropriate `WHERE` filtering condition.

In [11]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*) as total_rows
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE pickup_location IS NOT NULL

total_rows
0   174124804

In [12]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*) as total_rows
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE dropoff_location IS NOT NULL

total_rows
0   170672368

In [13]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*) as total_rows
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE trip_seconds > 0

total_rows
0   185678524

In [14]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*) as total_rows
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE trip_miles > 0

total_rows
0   154958725

Next, lets find out how many DISTINCT values we have for some of the categorical columns. Perhaps, this information will help us make informed decisions on selecting a subset from the dataset for further analysis.

In [15]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(DISTINCT(company)) AS num_companies, 
  COUNT(DISTINCT(EXTRACT(YEAR FROM trip_start_timestamp))) AS num_years, 
  COUNT(DISTINCT(taxi_id)) AS num_taxis, 
  COUNT(DISTINCT(payment_type)) AS num_payment_types, 
  COUNT(DISTINCT(pickup_location)) AS num_pickup_locations, 
  COUNT(DISTINCT(dropoff_location)) AS num_dropoff_locations
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`

num_companies  num_years  ...  num_pickup_locations  num_dropoff_locations
0            170          9  ...                   939                    962

[1 rows x 6 columns]

Does this mean we have 170 competitors? Far from it. Let’s write a simple query to understand this.

In [21]:
%%bigquery --project charming-layout-307403
SELECT 
  company, COUNT(unique_key) as total_trips
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE EXTRACT(YEAR FROM trip_start_timestamp) = 2021
GROUP BY company
ORDER BY total_trips DESC
LIMIT 10

company  total_trips
0                          Flash Cab       772392
1          Taxi Affiliation Services       723877
2                   Medallion Leasin       153340
3                           Sun Taxi       151780
4      Taxicab Insurance Agency, LLC       143063
5                       City Service       128338
6                Top Cab Affiliation        79761
7  Blue Ribbon Taxi Association Inc.        74907
8               Chicago Independents        73118
9                         Globe Taxi        63424

Selecting only the 3 most recent years and only the 4 topmost competitors (plus our company) brings the total number of rows down to only about 29.4 million. If we decide to be even more selective and pit ourselves only against our biggest competition “Taxi Affiliation Services”, then the total number of rows become only about 14.6 million.

In [22]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*)
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021

f0_
0  13355584

In [23]:
%%bigquery --project charming-layout-307403
SELECT 
  COUNT(*)
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Flash Cab"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021

f0_
0  9521074

# Prepare analytic datasets

It is important to first look at the overall trends. This query gives the total number of taxi trips per year between 2019 and 2021.

In [24]:
%%bigquery --project charming-layout-307403 trips_per_year
SELECT 
  EXTRACT(YEAR FROM trip_start_timestamp) AS year, COUNT(unique_key) as total_trips
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
GROUP BY year
ORDER BY total_trips DESC

In [25]:
trips_per_year

year  total_trips
0  2019     16477365
1  2020      3889032
2  2021      2576796

We also want to check how this trend for the top companies compare against the overall trend. Additionally, amongst top companies, we want to compare the yearly values of total number of taxis, average and total trip cost, average trip distance, average trip duration, and average tip received per trip.

As discussed in the previous subsection, some trips in the dataset have trip distance of 0 miles and some have trip duration of 0 seconds. Also, according to the dataset schema description for the `tip` column, “cash tips” have not been recorded in this dataset. Hence, we have to write separate queries with appropriate filters to extract the data in different DataFrames.

Lets first collect the total number of trips, total number of taxis, and average and total trip costs by `company` and `year`.

In [26]:
%%bigquery --project charming-layout-307403 trips_per_year_company
SELECT 
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  COUNT(unique_key) AS total_trips,
  COUNT(DISTINCT(taxi_id)) AS total_taxis,
  ROUND(AVG(trip_total), 2) AS avg_trip_cost,
  ROUND(SUM(trip_total), 2) AS sum_trip_cost,
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
GROUP BY year, company
ORDER BY year DESC, total_trips DESC

In [27]:
trips_per_year_company

year                        company  ...  avg_trip_cost  sum_trip_cost
0   2021                      Flash Cab  ...          23.06    17809192.25
1   2021      Taxi Affiliation Services  ...          22.64    16388972.05
2   2021               Medallion Leasin  ...          34.01     5214252.84
3   2021                       Sun Taxi  ...          28.41     4312375.76
4   2021  Taxicab Insurance Agency, LLC  ...          25.80     3690422.11
5   2020      Taxi Affiliation Services  ...          16.61    17502940.00
6   2020                      Flash Cab  ...          17.11    15406131.08
7   2020                       Sun Taxi  ...          18.43     4669482.48
8   2020               Medallion Leasin  ...          19.66     4592051.52
9   2020  Taxicab Insurance Agency, LLC  ...          17.01     2402740.89
10  2019      Taxi Affiliation Services  ...          16.80    60434251.33
11  2019                      Flash Cab  ...          17.91    44291421.87
12  2019                       Sun Taxi  ...          19.32    23696600.01
13  2019               Medallion Leasin  ...          22.15    25574354.92
14  2019  Taxicab Insurance Agency, LLC  ...          16.61     6253392.01

[15 rows x 6 columns]

Next, we get the average trip duration by `company` and `year` for taxi trips having non-zero duration.

In [28]:
%%bigquery --project charming-layout-307403 trips_seconds
SELECT 
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  ROUND(AVG(trip_seconds), 2) AS avg_trip_seconds
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
  AND trip_seconds > 0
GROUP BY year, company
ORDER BY year DESC, avg_trip_seconds DESC

In [29]:
trips_seconds

year                        company  avg_trip_seconds
0   2021                       Sun Taxi           1474.29
1   2021                      Flash Cab           1249.50
2   2021      Taxi Affiliation Services           1136.45
3   2021               Medallion Leasin           1116.70
4   2021  Taxicab Insurance Agency, LLC           1076.17
5   2020                      Flash Cab           1052.34
6   2020                       Sun Taxi            994.36
7   2020               Medallion Leasin            871.74
8   2020      Taxi Affiliation Services            834.58
9   2020  Taxicab Insurance Agency, LLC            776.05
10  2019                       Sun Taxi           1016.86
11  2019                      Flash Cab            991.17
12  2019               Medallion Leasin            925.09
13  2019  Taxicab Insurance Agency, LLC            850.64
14  2019      Taxi Affiliation Services            840.24

And, the average trip distance by `company` and `year` for taxi trips having non-zero distance.

In [30]:
%%bigquery --project charming-layout-307403 trips_miles
SELECT 
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  ROUND(AVG(trip_miles), 2) AS avg_trip_miles
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
  AND trip_miles > 0
GROUP BY year, company
ORDER BY year DESC, avg_trip_miles DESC

In [31]:
trips_miles

year                        company  avg_trip_miles
0   2021                       Sun Taxi            7.77
1   2021  Taxicab Insurance Agency, LLC            7.70
2   2021                      Flash Cab            7.18
3   2021               Medallion Leasin            6.65
4   2021      Taxi Affiliation Services            5.09
5   2020                      Flash Cab            5.10
6   2020  Taxicab Insurance Agency, LLC            4.64
7   2020                       Sun Taxi            4.60
8   2020               Medallion Leasin            4.24
9   2020      Taxi Affiliation Services            3.59
10  2019                      Flash Cab            4.92
11  2019                       Sun Taxi            4.81
12  2019  Taxicab Insurance Agency, LLC            4.38
13  2019               Medallion Leasin            4.32
14  2019      Taxi Affiliation Services            3.41

Finally, the average tips by `company` and `year` for non-cash payments.

In [32]:
%%bigquery --project charming-layout-307403 trips_tips
SELECT 
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  ROUND(AVG(tips), 2) AS avg_tips
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
  AND payment_type <> "Cash"
GROUP BY year, company
ORDER BY year DESC, avg_tips DESC

Since these 4 DataFrames hold data aggregated across the same 2 categories of `company` and `year`, joining them together into a single DataFrame will simplify things for the dashboard development step.

In [33]:
trips_per_year_company = trips_per_year_company.merge(trips_miles, on=['year', 'company'], how='left')
trips_per_year_company = trips_per_year_company.merge(trips_seconds, on=['year', 'company'], how='left')
trips_per_year_company = trips_per_year_company.merge(trips_tips, on=['year', 'company'], how='left')

We calculate additional metrics from this DataFrame: `avg_trip_miles_per_minute, avg_trip_cost_per_minute, avg_trip_cost_per_mile, total_trips_per_taxi.`

In [34]:
trips_per_year_company['avg_trip_miles_per_minute'] = round(trips_per_year_company['avg_trip_miles'] / trips_per_year_company['avg_trip_seconds'] * 60, 2)
trips_per_year_company['avg_trip_cost_per_minute'] = round(trips_per_year_company['avg_trip_cost'] / trips_per_year_company['avg_trip_seconds'] * 60, 2)
trips_per_year_company['avg_trip_cost_per_mile'] = round(trips_per_year_company['avg_trip_cost'] / trips_per_year_company['avg_trip_miles'], 2)
trips_per_year_company['total_trips_per_taxi'] = round(trips_per_year_company['total_trips'] / trips_per_year_company['total_taxis'], 2)

In [35]:
trips_per_year_company

year  ... total_trips_per_taxi
0   2021  ...              1602.47
1   2021  ...              1527.17
2   2021  ...              1267.27
3   2021  ...               744.02
4   2021  ...               905.46
5   2020  ...              1055.86
6   2020  ...              1316.15
7   2020  ...               675.87
8   2020  ...               865.30
9   2020  ...               771.71
10  2019  ...              2960.76
11  2019  ...              2976.52
12  2019  ...              3051.07
13  2019  ...              3299.74
14  2019  ...              2339.02

[15 rows x 13 columns]

Different companies may provide different payment options for their customers. Using the following query, we retrieve the total number of payments by `company, year` and `payment_type`.

In [36]:
%%bigquery --project charming-layout-307403 payment_types
SELECT
  COUNT(unique_key) AS total_payments,
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  payment_type
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
   "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
GROUP BY year, company, payment_type
ORDER BY year DESC, total_payments DESC

In [37]:
payment_types

total_payments  year                        company payment_type
0           311995  2021      Taxi Affiliation Services         Cash
1           304593  2021                      Flash Cab         Cash
2           263041  2021                      Flash Cab       Prcard
3           208296  2021      Taxi Affiliation Services      Unknown
4           203453  2021      Taxi Affiliation Services  Credit Card
..             ...   ...                            ...          ...
65            1191  2019  Taxicab Insurance Agency, LLC      Dispute
66             991  2019      Taxi Affiliation Services    No Charge
67             620  2019                      Flash Cab      Prepaid
68             273  2019                       Sun Taxi        Pcard
69              37  2019      Taxi Affiliation Services      Dispute

[70 rows x 4 columns]

Since our dataset is about taxi trips, analyzing location data can help reveal spatial and spatiotemporal patterns. We accumulate total number of trips by `company`, `year` and (`pickup_latitude`, `pickup_longitude`). We drop rows where pickup data is missing.

In [38]:
%%bigquery --project charming-layout-307403 trips_per_pickup
SELECT
  COUNT(unique_key) AS total_trips,
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  pickup_latitude AS latitude,
  pickup_longitude AS longitude
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
  AND pickup_latitude IS NOT NULL
  AND pickup_longitude IS NOT NULL
GROUP BY year, company, pickup_latitude, pickup_longitude
ORDER BY year DESC, total_trips DESC

In [39]:
trips_per_pickup

total_trips  year                        company   latitude  longitude
0          106108  2021                      Flash Cab  41.899602 -87.633308
1           91036  2021      Taxi Affiliation Services  41.899602 -87.633308
2           48380  2021      Taxi Affiliation Services  41.874005 -87.663518
3           46870  2021      Taxi Affiliation Services  41.980264 -87.913625
4           45464  2021                      Flash Cab  41.944227 -87.655998
...           ...   ...                            ...        ...        ...
4538            1  2019                      Flash Cab  41.801671 -87.594266
4539            1  2019                       Sun Taxi  42.005560 -87.901886
4540            1  2019  Taxicab Insurance Agency, LLC  41.916473 -87.641184
4541            1  2019      Taxi Affiliation Services  41.878644 -87.685132
4542            1  2019  Taxicab Insurance Agency, LLC  41.950673 -87.666536

[4543 rows x 5 columns]

And, we do the same for (`dropoff_latitude`, `dropoff_longitude`).

In [40]:
%%bigquery --project charming-layout-307403 trips_per_dropoff
SELECT
  COUNT(unique_key) AS total_trips,
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  company,
  dropoff_latitude AS latitude,
  dropoff_longitude AS longitude
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
    "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
  AND dropoff_latitude IS NOT NULL
  AND dropoff_longitude IS NOT NULL
GROUP BY year, company, dropoff_latitude, dropoff_longitude
ORDER BY year DESC, total_trips DESC

In [41]:
trips_per_dropoff

total_trips  year                    company   latitude  longitude
0           88392  2021                  Flash Cab  41.899602 -87.633308
1           79251  2021  Taxi Affiliation Services  41.899602 -87.633308
2           44851  2021  Taxi Affiliation Services  41.874005 -87.663518
3           42662  2021                  Flash Cab  41.944227 -87.655998
4           40599  2021                  Flash Cab  41.874005 -87.663518
...           ...   ...                        ...        ...        ...
6132            1  2019  Taxi Affiliation Services  41.949473 -87.771758
6133            1  2019           Medallion Leasin  41.855806 -87.674691
6134            1  2019                   Sun Taxi  41.986558 -87.713369
6135            1  2019           Medallion Leasin  41.700889 -87.600093
6136            1  2019                   Sun Taxi  41.776431 -87.637635

[6137 rows x 5 columns]

Lastly, concatenate the pickup and dropoff DataFrames.

In [42]:
trips_per_pickup['location_type'] = 'Pickup'
trips_per_dropoff['location_type'] = 'Dropoff'
trips_per_location = pd.concat([trips_per_pickup, trips_per_dropoff]).reset_index(drop=True)

In [43]:
trips_per_location

total_trips  year  ...  longitude  location_type
0           106108  2021  ... -87.633308         Pickup
1            91036  2021  ... -87.633308         Pickup
2            48380  2021  ... -87.663518         Pickup
3            46870  2021  ... -87.913625         Pickup
4            45464  2021  ... -87.655998         Pickup
...            ...   ...  ...        ...            ...
10675            1  2019  ... -87.771758        Dropoff
10676            1  2019  ... -87.674691        Dropoff
10677            1  2019  ... -87.713369        Dropoff
10678            1  2019  ... -87.600093        Dropoff
10679            1  2019  ... -87.637635        Dropoff

[10680 rows x 6 columns]

There could also be seasonal trends in the data. For further exploration, we extract the `trips_by_month` DataFrame.

In [44]:
%%bigquery --project charming-layout-307403 trips_by_month
SELECT
  COUNT(unique_key) AS total_trips,
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  EXTRACT(MONTH FROM TIMESTAMP_TRUNC(trip_start_timestamp, MONTH)) AS month,
  company
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
   "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
GROUP BY year, company, month
ORDER BY year DESC, total_trips DESC

In [45]:
trips_by_month

total_trips  year  month                        company
0         113775  2021      9                      Flash Cab
1         112259  2021      8                      Flash Cab
2         109483  2021      9      Taxi Affiliation Services
3         108178  2021      7                      Flash Cab
4         105925  2021      8      Taxi Affiliation Services
..           ...   ...    ...                            ...
165        30269  2019      5  Taxicab Insurance Agency, LLC
166        22451  2019      4  Taxicab Insurance Agency, LLC
167        21500  2019      3  Taxicab Insurance Agency, LLC
168        18305  2019      2  Taxicab Insurance Agency, LLC
169        14845  2019      1  Taxicab Insurance Agency, LLC

[170 rows x 4 columns]

Similar to seasonal trends, there could also be distinct trends in operating hours for different taxi companies in Chicago. Therefore, we put together this data in the `trips_by_date_hour` DataFrame.

In [46]:
%%bigquery --project charming-layout-307403 trips_by_date_hour
SELECT
  COUNT(unique_key) AS total_trips,
  COUNT(DISTINCT(taxi_id)) AS total_taxis,
  EXTRACT(YEAR FROM trip_start_timestamp) AS year,
  EXTRACT(DATE FROM trip_start_timestamp) AS date,
  EXTRACT(HOUR FROM TIMESTAMP_TRUNC(trip_start_timestamp, HOUR)) AS hour,
  company
FROM `bigquery-public-data.chicago_taxi_trips.taxi_trips`
WHERE company 
  IN (
   "Taxi Affiliation Services",
    "Taxicab Insurance Agency, LLC",
    "Flash Cab",
    "Medallion Leasin",
    "Sun Taxi"
  )
  AND EXTRACT(YEAR FROM trip_start_timestamp) BETWEEN 2019 AND 2021
GROUP BY year, company, date, hour
ORDER BY year DESC, total_trips DESC

Unlike `trips_by_month`, notice that for `trips_by_date_hour`, we have also grouped the trips by `DATE`. We have done this because we also want to find the average number of trips per taxi by `hour, year` and `company`.

In [47]:
trips_by_date_hour = trips_by_date_hour.groupby(by=['year', 'hour', 'company']).mean().reset_index()
trips_by_date_hour['total_trips'] = round(trips_by_date_hour['total_trips'], 2)
trips_by_date_hour['total_taxis'] = round(trips_by_date_hour['total_taxis'], 2)
trips_by_date_hour = trips_by_date_hour.rename(columns={'total_trips': 'avg_number_of_trips', 'total_taxis': 'avg_number_of_taxis'})
trips_by_date_hour['avg_number_of_trips_per_taxi'] = round(trips_by_date_hour['avg_number_of_trips'] / trips_by_date_hour['avg_number_of_taxis'], 2)

In [48]:
trips_by_date_hour

year  hour  ... avg_number_of_taxis  avg_number_of_trips_per_taxi
0    2019     0  ...              103.32                          1.65
1    2019     0  ...               40.85                          1.70
2    2019     0  ...               32.74                          1.59
3    2019     0  ...              166.70                          1.69
4    2019     0  ...                9.91                          1.57
..    ...   ...  ...                 ...                           ...
355  2021    23  ...               43.32                          1.61
356  2021    23  ...               11.41                          1.50
357  2021    23  ...               12.56                          1.67
358  2021    23  ...               43.94                          1.45
359  2021    23  ...                9.85                          1.32

[360 rows x 6 columns]

And that’s it! That’s all the data we need for the next step of our analysis.

## Download the csv files

In [49]:
trips_by_date_hour.to_csv('trips_by_hour.csv', index=None)
trips_per_year_company.to_csv('trips_by_year_company.csv', index=None)
trips_per_year.to_csv('trips_per_year.csv', index=None)
trips_per_location.to_csv('trips_per_location.csv', index=None)
payment_types.to_csv('payment_types.csv', index=None)
trips_by_month.to_csv('trips_by_month.csv', index=None)

In [50]:
files.download("trips_by_hour.csv")
files.download("trips_by_year_company.csv")
files.download("trips_per_year.csv")
files.download("trips_per_location.csv")
files.download("payment_types.csv")
files.download("trips_by_month.csv")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>